
# Self-Organizing Map

In this example, we illustrate the use of the :class:`.SOM` plot
on the Sobieski's SSBJ problem.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.problems.sobieski.core.problem import SobieskiProblem

## Import
The first step is to import some high-level functions
and a method to get the design space.



In [ ]:
configure_logger()

## Description

The :class:`.SOM` post-processing performs a Self Organizing Map
clustering on the optimization history.
A :class:`.SOM` is a 2D representation of a design of experiments
which requires dimensionality reduction since it may be in a very high dimension.

A :term:`SOM` is built by using an unsupervised artificial neural network
:cite:`Kohonen:2001`.
A map of size ``n_x.n_y`` is generated, where
``n_x`` is the number of neurons in the $x$ direction and ``n_y``
is the number of neurons in the $y$ direction. The design space
(whatever the dimension) is reduced to a 2D representation based on
``n_x.n_y`` neurons. Samples are clustered to a neuron when their design
variables are close in terms of their L2 norm. A neuron is always located at the
same place on a map. Each neuron is colored according to the average value for
a given criterion. This helps to qualitatively analyze whether parts of the design
space are good according to some criteria and not for others, and where
compromises should be made. A white neuron has no sample associated with
it: not enough evaluations were provided to train the SOM.

SOM's provide a qualitative view of the :term:`objective function`, the
:term:`constraints`, and of their relative behaviors.



## Create disciplines
At this point, we instantiate the disciplines of Sobieski's SSBJ problem:
Propulsion, Aerodynamics, Structure and Mission



In [ ]:
disciplines = create_discipline(
    [
        "SobieskiPropulsion",
        "SobieskiAerodynamics",
        "SobieskiStructure",
        "SobieskiMission",
    ]
)

## Create design space
We also read the design space from the :class:`.SobieskiProblem`.



In [ ]:
design_space = SobieskiProblem().design_space

## Create and execute scenario
The next step is to build an MDO scenario in order to maximize the range,
encoded 'y_4', with respect to the design parameters, while satisfying the
inequality constraints 'g_1', 'g_2' and 'g_3'. We can use the MDF formulation,
the Monte Carlo DOE algorithm and 30 samples.



In [ ]:
scenario = create_scenario(
    disciplines,
    formulation="MDF",
    objective_name="y_4",
    maximize_objective=True,
    design_space=design_space,
    scenario_type="DOE",
)
scenario.set_differentiation_method()
for constraint in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(constraint, "ineq")
scenario.execute({"algo": "OT_MONTE_CARLO", "n_samples": 30})

## Post-process scenario
Lastly, we post-process the scenario by means of the
:class:`.SOM` plot which performs a self organizing map
clustering on optimization history.



.. tip::

   Each post-processing method requires different inputs and offers a variety
   of customization options. Use the high-level function
   :func:`.get_post_processing_options_schema` to print a table with
   the options for any post-processing algorithm.
   Or refer to our dedicated page:
   `gen_post_algos`.



In [ ]:
scenario.post_process("SOM", save=False, show=True)

Figure `fig-ssbj-mdf-som100` illustrates another :term:`SOM` on the Sobieski
use case. The optimization method is a (costly) derivative free algorithm
(``NLOPT_COBYLA``), indeed all the relevant information for the optimization
is obtained at the cost of numerous evaluations of the functions. For
more details, please read the paper by
:cite:`kumano2006multidisciplinary` on wing MDO post-processing
using SOM.


.. figure:: /tutorials/ssbj/figs/MDOScenario_SOM_v100.png
    :scale: 10 %

    SOM example on the Sobieski problem.

A DOE may also be a good way to produce SOM maps.
Figure `fig-ssbj-mdf-som10000` shows an example with 10000 points on
the same test case. This produces more relevant SOM plots.


.. figure:: /tutorials/ssbj/figs/som_fine.png
    :scale: 55 %

    SOM example on the Sobieski problem with a 10 000 samples DOE.

